In [1]:
pip install pandas

Defaulting to user installation because normal site-packages is not writeable
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.0/13.0 MB 1.7 MB/s eta 0:00:00m eta 0:00:010:00:01m
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.2/18.2 MB 1.5 MB/s eta 0:00:00m eta 0:00:010:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 345.4/345.4 KB 2.9 MB/s eta 0:00:003.2 MB/s eta 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install scipy

Defaulting to user installation because normal site-packages is not writeable
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 38.6/38.6 MB 1.2 MB/s eta 0:00:00m eta 0:00:010:00:01m
Note: you may need to restart the kernel to use updated packages.


In [3]:
pip install scikit-learn

Defaulting to user installation because normal site-packages is not writeable
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.1/12.1 MB 638.6 kB/s eta 0:00:00m eta 0:00:010:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 301.8/301.8 KB 459.6 kB/s eta 0:00:00 kB/s eta 0:00:01:01
Note: you may need to restart the kernel to use updated packages.


In [4]:
pip install librosa

Defaulting to user installation because normal site-packages is not writeable
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 260.0/260.0 KB 211.2 kB/s eta 0:00:001m222.7 kB/s eta 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 63.0/63.0 KB 1.5 MB/s eta 0:00:000:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 791.0 kB/s eta 0:00:001m785.3 kB/s eta 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 938.8 kB/s eta 0:00:00m eta 0:00:010:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 385.1/385.1 KB 1.3 MB/s eta 0:00:000:00:010:00:01:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 1.2 MB/s eta 0:00:00m eta 0:00:010:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.8/43.8 MB 972.5 kB/s eta 0:00:00m eta 0:00:010:00:02
Note: you may need to restart the kernel to use updated packages.


In [5]:
pip install pymongo

Defaulting to user installation because normal site-packages is not writeable
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 670.0/670.0 KB 141.7 kB/s eta 0:00:001m139.3 kB/s eta 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 307.7/307.7 KB 175.4 kB/s eta 0:00:001m176.7 kB/s eta 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [12]:
import os
import librosa
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from pymongo import MongoClient

# Function to extract audio features from MP3 files
def extract_features(file_path):
    try:
        # Load audio file
        y, sr = librosa.load(file_path)
        # Extract features (MFCC, spectral centroid, zero-crossing rate)
        mfcc = librosa.feature.mfcc(y=y, sr=sr)
        spectral_centroid = librosa.feature.spectral_centroid(y=y, sr=sr)
        zero_crossing_rate = librosa.feature.zero_crossing_rate(y)
        # Concatenate features into a single array
        features = np.concatenate((mfcc, spectral_centroid, zero_crossing_rate), axis=0)
        return features
    except Exception as e:
        print(f"Error processing file {file_path}: {e}")
        return None

# Function to preprocess features (standardization)
def preprocess_features(features):
    # Standardize features
    scaler = StandardScaler()
    features_standardized = scaler.fit_transform(features.T).T
    return features_standardized

# Function to apply dimensionality reduction (PCA)
def apply_pca(features, n_components=None):
    if n_components is None:
        n_components = min(features.shape)
    pca = PCA(n_components=n_components)
    features_pca = pca.fit_transform(features.T).T
    return features_pca

# Function to connect to MongoDB and insert data
def insert_to_mongodb(features):
    try:
        # Connect to MongoDB
        client = MongoClient('mongodb://127.0.0.1:27017/')
        db = client['music_recommendation']
        collection = db['audio_features']
        # Insert features into MongoDB
        collection.insert_one({"features": features.tolist()})
        print("Data inserted into MongoDB successfully!")
    except Exception as e:
        print(f"Error inserting data into MongoDB: {e}")

# Main function
# Main function
def main():
    # Directory containing the MP3 files
    dataset_path = "/media/hdoop/C6760CE6760CD8D7/BDA PROJECT/fma_large"  # Update this path
    # Iterate through each folder (000 to 155)
    for folder_index in range(156):  # Loop from 0 to 155
        # Format the folder index to have leading zeros
        folder_name = f"{folder_index:03d}"
        folder_path = os.path.join(dataset_path, folder_name)
        if os.path.isdir(folder_path):
            print(f"Processing files in folder {folder_name}...")
            # Iterate through each MP3 file in the folder
            for file_name in os.listdir(folder_path):
                if file_name.endswith(".mp3"):
                    file_path = os.path.join(folder_path, file_name)
                    # Extract features from the MP3 file
                    features = extract_features(file_path)
                    if features is not None:
                        # Preprocess features (standardization)
                        features_standardized = preprocess_features(features)
                        # Apply dimensionality reduction (PCA)
                        features_pca = apply_pca(features_standardized)
                        # Insert features into MongoDB
                        insert_to_mongodb(features_pca)

if __name__ == "__main__":
    main()


Processing files in folder 000...
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into Mong

/home/hdoop/.local/lib/python3.10/site-packages/sklearn/decomposition/_pca.py:559: RuntimeWarning: invalid value encountered in divide
  explained_variance_ratio_ = explained_variance_ / total_var


Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted in

/tmp/ipykernel_40650/1483843.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  y, sr = librosa.load(file_path)
[src/libmpg123/parse.c:do_readahead():1099] warning: Cannot read next header, a one-frame stream? Duh...
/home/hdoop/.local/lib/python3.10/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)


Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted in

...

Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted in

Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted in

Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted in

Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted into MongoDB successfully!
Data inserted in

KeyboardInterrupt: 

In [10]:
import os
from pymongo import MongoClient

def get_actual_folders(dataset_path):
    actual_folders = set()
    for folder_name in os.listdir(dataset_path):
        if folder_name.isdigit():
            actual_folders.add(int(folder_name))
    return actual_folders

def cleanup_mongodb(dataset_path):
    try:
        # Connect to MongoDB
        client = MongoClient('mongodb://localhost:27017/')
        db = client['music_recommendation']
        collection = db['audio_features']
        
        # Get actual folders present in the dataset directory
        actual_folders = get_actual_folders(dataset_path)
        
        # Define the range of expected folders
        expected_folders = set(range(156))  # Assuming folders are numbered from 0 to 155
        
        # Find the intersection of actual and expected folders
        folders_to_cleanup = actual_folders - expected_folders
        
        # Query MongoDB to find documents with folder numbers beyond the expected range
        # Assuming folder numbers are stored in a field named "folder_number"
        query = {"folder_number": {"$in": list(folders_to_cleanup)}}
        unwanted_documents = collection.find(query)
        
        # Delete unwanted documents
        for doc in unwanted_documents:
            collection.delete_one({"_id": doc["_id"]})
        
        print("Data cleanup completed successfully!")
        
    except Exception as e:
        print(f"Error cleaning up MongoDB data: {e}")

if __name__ == "__main__":
    # Directory containing the MP3 files
    dataset_path = "D:/BDA PROJECT/fma_large"
    cleanup_mongodb(dataset_path)


Data cleanup completed successfully!


In [13]:
from pymongo import MongoClient

# Connect to MongoDB
client = MongoClient('mongodb://localhost:27017/')
db = client['music_recommendation']
collection = db['audio_features']

# Check if documents are present
num_documents = collection.count_documents({})
print(f"Number of documents in collection: {num_documents}")

# Inspect document structure
sample_document = collection.find_one()
print("Sample Document:")
print(sample_document)

# Optionally, compare with original data and visualize features
# Your implementation for comparison and visualization goes here


Number of documents in collection: 104478
Sample Document:
{'_id': ObjectId('663cfc46eff9941de22bb6c9'), 'features': [[3.6756520370513175, 3.1075330221641035, 2.849467203982779, 3.690719499090858, 3.005603611856387, 1.626903043966636, 1.4197085906123699, 1.9490394774253375, 2.428120655276948, 3.421287838604521, 3.0229115270134455, 1.8215302519612315, 2.084308650284516, 2.3806818279463346, 2.6058936561931954, 2.8736833270235294, 2.308515208992898, 1.8461054050411718, 2.7810461906392514, 3.3950632557590463, 3.5629310461350663, 4.839701035721745, 5.404555670361576, 1.9129798546173395, -1.8020211340947851, -2.9872277995601926, -2.7288455936978653, -1.9716437120327985, -2.254794869730025, -1.9601980219183401, -1.2922452043034942, -0.6082570455890153, -0.37331522908751325, 1.0973361721040358, 2.640509315676927, 2.0353418839423587, 1.4573948823312426, 0.9053390223474287, 0.05399404089261377, -0.32584223925993644, -1.1126125436548369, -0.5719657761010537, 0.6077238636984629, 0.5153315382200649

In [14]:
pip install pyspark

Defaulting to user installation because normal site-packages is not writeable
ERROR: Could not find a version that satisfies the requirement pyspark (from versions: none)
ERROR: No matching distribution found for pyspark
Note: you may need to restart the kernel to use updated packages.


In [4]:
pip install numpy

  Using cached numpy-1.26.4-cp310-cp310-win_amd64.whl.metadata (61 kB)
Using cached numpy-1.26.4-cp310-cp310-win_amd64.whl (15.8 MB)
Note: you may need to restart the kernel to use updated packages.


In [2]:
import pyspark
from pyspark.sql import SparkSession

# Ensure the path to the JAR files are correct and accessible
path_to_mongo_spark_connector = "/home/hdoop/Downloads/mongo-spark-connector_2.12-3.0.2.jar"
path_to_mongo_java_driver = "/home/hdoop/Downloads/mongo-java-driver-3.12.10.jar"

print("Creating SparkSession...")

spark = SparkSession.builder \
    .appName("MusicRecommendation") \
    .config("spark.mongodb.input.uri", "mongodb://127.0.0.1/music_recommendation.audio_features") \
    .config("spark.mongodb.output.uri", "mongodb://127.0.0.1/music_recommendation.audio_features") \
    .config("spark.jars", ",".join([path_to_mongo_spark_connector, path_to_mongo_java_driver])) \
    .getOrCreate()
print("SparkSession created successfully.")


Creating SparkSession...


24/05/11 13:52:28 WARN Utils: Your hostname, irtaza-Victus-by-HP-Gaming-Laptop-15-fa0xxx resolves to a loopback address: 127.0.1.1; using 2407:d000:d:7347:994a:52ef:638:15a instead (on interface wlp4s0)
24/05/11 13:52:28 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
24/05/11 13:52:28 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).


SparkSession created successfully.


In [4]:
spark.stop()

In [3]:
# Load preprocessed audio features from MongoDB into a Spark DataFrame
print("Loading data from MongoDB...")
audio_features = spark.read.format("mongo").option("uri", "mongodb://127.0.0.1:27017/music_recommendation.audio_features").load()
print("Data loaded successfully.")

Loading data from MongoDB...


Data loaded successfully.


In [ ]:
# Print the size of the data
print("Size of the loaded data: {} rows x {} columns".format(audio_features.count(), len(audio_features.columns)))

# Print the columns
print("Columns in the DataFrame:")
for col_name in audio_features.columns:
    print(col_name)

# Show the first 50 rows
print("First 50 rows of the DataFrame:")
audio_features.show(50)

Size of the loaded data: 104478 rows x 2 columns
Columns in the DataFrame:
_id
features
First 50 rows of the DataFrame:


In [3]:
# Split the data into training and testing sets
print("Splitting data into training and testing sets...")
# Define the ratio for splitting (e.g., 80% training, 20% testing)
training_ratio = 0.8
testing_ratio = 1.0 - training_ratio

# Split the data
training_data, test_data = audio_features.randomSplit([training_ratio, testing_ratio], seed=1234)

# Indicate when data splitting is done
print("Data splitting completed.")


Splitting data into training and testing sets...
Data splitting completed.


In [4]:
print(training_data)


DataFrame[_id: struct<oid:string>, features: array<array<double>>]


In [ ]:
# Show a sample of the training data
print("Sample of the training data:")
training_data.show(50)


Sample of the training data:


In [14]:
from pyspark.sql.functions import col

# Add a unique identifier column to the DataFrame
audio_features = audio_features.withColumn("row_id", monotonically_increasing_id())

# Split the 'features' column into separate columns for user_id, track_id, and play_count
audio_features = audio_features.select("row_id", 
                                       col("user_id"),
                                       col("track_id"),
                                       col("play_count"))

# Drop rows with null values (if any)
audio_features = audio_features.na.drop()

# Show the updated DataFrame
print("Updated DataFrame after splitting features:")
audio_features.show()

# Indicate when data transformation is done
print("Data transformation completed.")


Updated DataFrame after splitting features:
+------+--------------------+--------------------+--------------------+
|row_id|             user_id|            track_id|          play_count|
+------+--------------------+--------------------+--------------------+
|     0|[3.67565203705131...|[1.41961761472949...|[0.59528011781251...|
|     1|[-4.0598436407253...|[-3.1586673033515...|[2.24658736130245...|
|     2|[-0.6841017950883...|[2.12205865664366...|[-1.9330350240235...|
|     3|[-1.2782707210287...|[-1.5050489833884...|[2.35206539729295...|
|     4|[-1.4471050947071...|[0.77177342817203...|[5.53291067952867...|
|     5|[-2.7510797544587...|[1.29887764531005...|[-2.1107413662622...|
|     6|[-1.5010832185205...|[0.03675751622224...|[-1.0067368727045...|
|     7|[1.22662899283504...|[-1.2336217329932...|[-4.2421677835376...|
|     8|[-2.0315676181775...|[1.44878320030728...|[5.20380442875847...|
|     9|[-1.7078368728266...|[-1.8421218428156...|[1.19464083784140...|
|    10|[1.307634124

In [21]:
from pyspark.sql.functions import col, split, monotonically_increasing_id


# Assuming audio_features is your DataFrame

# Add a unique identifier column to the DataFrame
audio_features = audio_features.withColumn("row_id", monotonically_increasing_id())

# Split the 'features' column into separate columns for user_id, track_id, and play_count
audio_features = audio_features.withColumn("user_id", split(col("user_id"), " ")[0].cast("int"))
audio_features = audio_features.withColumn("track_id", split(col("track_id"), " ")[0].cast("int"))
audio_features = audio_features.withColumn("play_count", split(col("play_count"), " ")[0].cast("int"))

# Drop rows with null values
audio_features = audio_features.dropna()

# Show summary of cleaned data
audio_features.summary().show()

# Indicate when data transformation is done
print("Data transformation completed.")



24/05/11 01:55:35 WARN SparkStringUtils: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.


+-------+--------------------+-------------------+-------------------+-------------------+
|summary|              row_id|            user_id|           track_id|         play_count|
+-------+--------------------+-------------------+-------------------+-------------------+
|  count|              104372|             104372|             104372|             104372|
|   mean|2.469210738319892...|0.17473077070478674|0.23581037059747825|0.26349978921549844|
| stddev|1.438479632224062...|  2.509676847954934| 2.1740222181530235| 1.9443672087385842|
|    min|                   0|                -12|                -13|                -14|
|    25%|       1202590842938|                 -1|                 -1|                 -1|
|    50%|       2473901162563|                  0|                  0|                  0|
|    75%|       3719441678394|                  1|                  1|                  1|
|    max|       4964982194215|                 58|                 48|                 31|

In [22]:
from pyspark.ml.recommendation import ALS
from pyspark.ml.evaluation import RegressionEvaluator

# Create an ALS instance
als = ALS(maxIter=10, regParam=0.01, userCol="user_id", itemCol="track_id", ratingCol="play_count",
          coldStartStrategy="drop")

# Split the data into training and test sets
(training_data, test_data) = audio_features.randomSplit([0.8, 0.2])

# Train the ALS model
print("Training the ALS model...")
model = als.fit(training_data)
print("Model training completed.")

Training the ALS model...


24/05/11 02:04:57 WARN InstanceBuilder: Failed to load implementation from:dev.ludovic.netlib.blas.JNIBLAS
24/05/11 02:04:57 WARN InstanceBuilder: Failed to load implementation from:dev.ludovic.netlib.lapack.JNILAPACK


Model training completed.


In [24]:
# Print model parameters
print("Model Parameters:")
print("maxIter:", model._java_obj.parent().getMaxIter())
print("regParam:", model._java_obj.parent().getRegParam())
print("userCol:", model._java_obj.parent().getUserCol())
print("itemCol:", model._java_obj.parent().getItemCol())
print("ratingCol:", model._java_obj.parent().getRatingCol())
print("coldStartStrategy:", model._java_obj.parent().getColdStartStrategy())


Model Parameters:
maxIter: 10
regParam: 0.01
userCol: user_id
itemCol: track_id
ratingCol: play_count
coldStartStrategy: drop


In [27]:
from pyspark.ml.recommendation import ALS
from pyspark.ml.evaluation import RegressionEvaluator

predictions = model.transform(test_data)

# Evaluate the model using an appropriate evaluation metric
evaluator = RegressionEvaluator(
    metricName="rmse",
    labelCol="play_count",
    predictionCol="prediction"
)

# Calculate the RMSE
rmse = evaluator.evaluate(predictions)
print("Root Mean Squared Error (RMSE) = ", rmse)

Root Mean Squared Error (RMSE) =  1.9263181378406866


In [33]:
print("Root Mean Squared Error (RMSE) = " + str(rmse))


Root Mean Squared Error (RMSE) = 1.9263181378406866


In [5]:
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder
from pyspark.sql import SparkSession

# Create a SparkSession
spark = SparkSession.builder \
    .appName("Hyper") \
    .getOrCreate()

# Define the ALS model
als = ALS(userCol="user_id", itemCol="track_id", ratingCol="play_count",
          coldStartStrategy="drop")

# Define the parameter grid for hyperparameter tuning
param_grid = ParamGridBuilder() \
    .addGrid(als.rank, [5, 10, 15]) \
    .addGrid(als.maxIter, [10, 15, 20]) \
    .addGrid(als.regParam, [0.01, 0.05, 0.1]) \
    .build()

# Define the evaluator
evaluator = RegressionEvaluator(metricName="rmse", labelCol="play_count",
                                predictionCol="prediction")

# Define the cross-validator
cross_validator = CrossValidator(estimator=als,
                                 estimatorParamMaps=param_grid,
                                 evaluator=evaluator,
                                 numFolds=5)  # You can adjust the number of folds

# Perform cross-validation
print("Performing hyperparameter tuning...")
cv_model = cross_validator.fit(training_data)
print("Hyperparameter tuning completed.")




24/05/11 02:49:39 WARN Utils: Your hostname, irtaza-Victus-by-HP-Gaming-Laptop-15-fa0xxx resolves to a loopback address: 127.0.1.1; using 2407:d000:d:7347:1f6:8a1b:6c9f:fa68 instead (on interface wlp4s0)
24/05/11 02:49:39 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
24/05/11 02:49:39 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


NameError: name 'RegressionEvaluator' is not defined

In [27]:
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder
from pyspark.ml.evaluation import RegressionEvaluator  # Import RegressionEvaluator
(training_data, test_data) = audio_features.randomSplit([0.8, 0.2])

# Define the ALS model
als = ALS(userCol="user_id", itemCol="track_id", ratingCol="play_count",
          coldStartStrategy="drop")

# Define the parameter grid for hyperparameter tuning
param_grid = ParamGridBuilder() \
    .addGrid(als.rank, [5, 10, 15]) \
    .addGrid(als.maxIter, [10, 15, 20]) \
    .addGrid(als.regParam, [0.01, 0.05, 0.1]) \
    .build()

# Define the evaluator
evaluator = RegressionEvaluator(metricName="rmse", labelCol="play_count",
                                predictionCol="prediction")

# Define the cross-validator
cross_validator = CrossValidator(estimator=als,
                                 estimatorParamMaps=param_grid,
                                 evaluator=evaluator,
                                 numFolds=5)  # You can adjust the number of folds

# Perform cross-validation
print("Performing hyperparameter tuning...")
cv_model = cross_validator.fit(training_data)
print("Hyperparameter tuning completed.")


NameError: name 'audio_features' is not defined

In [ ]:
# Get the best model from cross-validation
best_model = cv_model.bestModel

# Evaluate the best model on the test data
predictions = best_model.transform(test_data)
rmse = evaluator.evaluate(predictions)
print("Root Mean Squared Error (RMSE) for best model:", rmse)

# Get the best hyperparameters
best_rank = best_model.rank
best_max_iter = best_model._java_obj.parent().getMaxIter()
best_reg_param = best_model._java_obj.parent().getRegParam()

print("Best hyperparameters:")
print("- Rank:", best_rank)
print("- Max Iterations:", best_max_iter)
print("- Regularization Parameter:", best_reg_param)


In [1]:
spark.stop()

NameError: name 'spark' is not defined